In [1]:
import pandas as pd
import folium
from folium import Marker
from folium.plugins import MarkerCluster
import sqlalchemy as dbs
import pymysql
from datetime import datetime


cluster = MarkerCluster()
con = pymysql.connect(host='kingsms.asuscomm.com', port=3309, user='root', password='1!Tjalstjs', db='firebase', charset='utf8') # 한글처리 (charset = 'utf8')
 # STEP 3: Connection 으로부터 Cursor 생성
cur = con.cursor()
# STEP 4: SQL문 실행 및 Fetch
sql = "SELECT substr(gps_time, 9, 25) gps_time, trim(gps_latitude), trim(gps_longitude)  FROM gps_history  limit 10000"
cur.execute(sql)

rows = cur.fetchall()

row_cnt = cur.rowcount  

con.close()

df = pd.DataFrame(rows) # 쿼리 결과를 dataframe으로 저장

center = [37.306862,  126.9834126]
map = folium.Map(location=center, zoom_start=15)

lines = df[[1,2]].astype(float).values[:].tolist()
times = df[0].apply(lambda _ : datetime.strptime(_,'%Y-%m-%d %H:%M:%S')).tolist()

print(times[0])
print(times[-1])
total_time = (times[0]-times[-1])
print(total_time)

folium.PolyLine(locations = lines).add_to(map)

over_times = [] #30초 이상 머무른 시간
over_gps = [] # 장소


for i in range(row_cnt-1):
    temp = (times[i]-times[i+1]).seconds
    # 몇초 멈춘걸 의미 있게 볼 것 인가?
    if temp > 30:
        over_gps.append(lines[i])
        over_times.append(temp)

for i in range(len(over_gps)):
#     folium.CircleMarkerlocation = over_gps[i], tooltip = str(over_times[i])+"초", radius = 10 ,  color='#FF2D00', fill_color='#F38168').add_to(m)

    cluster.add_child(           
#             Marker(location = over_gps[i], popup = "<pre>" + "라벨" + "<br>" + "</pre>",)).add_to(map)
            Marker(location = over_gps[i], popup = "<pre>" + over_times[i] + "<br>" + "</pre>",)).add_to(map)

# print(over_times)   
# print(over_gps)

map

# for row in rows:
#     if row[0] is not None:
# #         fg.add_child(folium.Marker(location=[row[1],row[2]],popup="volcanoes",icon=folium.Icon(color="green")))
# #         cluster.add_child(fg)
    
#         folium.PolyLine(locations = lines).add_to(map)
    
# #         gps_latitude = row[1]
# #         gps_longitude = row[2]
# #         cluster.add_child(            
# # #         Marker(location = [gps_latitude, gps_latitude], popup = "<pre>" + "라벨" + "<br>" + "</pre>",)).add_to(map)
# #         Marker(location = [row[1], row[2]], popup = "<pre>" + row[0] + "<br>" + "</pre>",)).add_to(map)
#     else :
#         max_date = "2022-12-01 01"

# # map

# folium.PolyLine(locations = lines).add_to(m)


2024-03-17 11:01:07
2024-03-17 16:02:36
-1 days +18:58:31
